In [ ]:
from pyspark.sql.functions import col,trim
from datetime import date
import pandas as pd

#### Extraction of FTEx taken by the shipments

In [ ]:
#add cy of reciept and delivery
df_shipment = spark.sql(""" select distinct dimship.SHIPMENT_NO, dimship.SHIPMENT_STATUS_DESC, dimship.LAST_CONFIRMED_TS, dimship.PRICE_CALC_DT, dimship.FK_SHIPMENT_VERSION, OPERATOR_DESC, spot_YN from dnd.dim_shipment_new  as  dimship where dimship.spot_YN = 'Y' and dimship.SHIPMENT_STATUS_DESC in ('Active','Completed') and dimship.BOOKED_TS >= '2021-06-01' and RECEIPT_SERVICE_MODE_CD = 'CY' and DELIVERY_SERVICE_MODE_CD = 'CY' """)

df_afls_price = spark.sql(""" select distinct  FK_SHIPMENT_VERSION, INSTANCE_ID from dnd.afls_price_prod """)

df_afls_price_element = spark.sql(""" select distinct element.INSTANCE_ID, element.FK_AFLS_PRICE, element.FK_AFLS_CHARGE_TYPES, element.date_part from dnd.afls_price_element_new as element """)

df_shipment_price = df_shipment.join(df_afls_price,df_afls_price.FK_SHIPMENT_VERSION==df_shipment.FK_SHIPMENT_VERSION)

df_shipment_price_element=df_shipment_price.join(df_afls_price_element,df_shipment_price.INSTANCE_ID ==df_afls_price_element.FK_AFLS_PRICE)

df_combination_1 = df_shipment_price_element.filter(df_shipment_price_element.FK_AFLS_CHARGE_TYPES.isin(['F01','F02','F03','F04','F05','F06','F07','F08','F09','F10','F11','F12','F13','F14'])).drop("SOURCE_TXN_TYPE","INSTANCE_ID","FK_SHIPMENT_VERSION","FK_AFLS_PRICE").dropDuplicates()
df_combination_1.createOrReplaceTempView("df_combination_1")

In [ ]:
df_combination_spot1=spark.sql(""" select *
from (select *,row_number() over (partition by SHIPMENT_NO  ORDER BY date_part desc)  as seqnum from df_combination_1 
     ) a
where seqnum <=1
order by a.date_part asc; """)
df_combination_spot1.createOrReplaceTempView("df_combination_spot1")

In [ ]:
df_shipment_equipment=spark.sql(""" select distinct SHIPMENT_NO,CONTAINER_NO as Equipment_No from dnd.shipment_equipment_new """)

df_combination_equipment = df_combination_spot1.join(df_shipment_equipment,(df_combination_spot1.SHIPMENT_NO == df_shipment_equipment.SHIPMENT_NO) ,"inner").drop(df_shipment_equipment.SHIPMENT_NO)
df_combination_equipment.createOrReplaceTempView("df_combination_equipment")

df_combination_equipment = spark.sql(""" select distinct OPERATOR_DESC, spot_YN,SHIPMENT_NO, Equipment_No, FK_AFLS_CHARGE_TYPES  from df_combination_equipment """)
df_combination_equipment.createOrReplaceTempView("df_combination_equipment")

#### Extraction of CDET Days

In [ ]:
shipment = spark.sql(""" select distinct OPERATOR_DESC, BOOKED_TS, PRICE_CALC_DT, SUBSTRING(DIPLA_CITY_CD, 1, 2) AS Import_Country, LOPFI_CITY_CD, DIPLA_CITY_CD, CONSIGNEE_CUSTOMER_CD, BOOKED_BY_CUSTOMER_CD, SHIPMENT_NO, CONTAINER_CNT, Spot_YN  from dnd.dim_shipment_new where RECEIPT_SERVICE_MODE_CD = 'CY' and DELIVERY_SERVICE_MODE_CD = 'CY' and OPERATOR_CD in ('MSL')  and SHIPMENT_STATUS_DESC in ('Active', 'Completed') 
and BOOKED_TS >= '2021-06-01' """)
shipment.createOrReplaceTempView("shipment")

equipment = spark.sql(""" select distinct SHIPMENT_NO, CONTAINER_NO, CONTAINER_TYPE_CD, CONTAINER_SIZE_CD, BOOKED_FFE from  dnd.shipment_equipment_new """)
equipment.createOrReplaceTempView("equipment")

ship_equip = shipment.join(equipment, (shipment.SHIPMENT_NO == equipment.SHIPMENT_NO), 'inner').drop(equipment.SHIPMENT_NO)
ship_equip.createOrReplaceTempView("ship_equip")


In [ ]:
dnd_freetime1_v4 = spark.read.format("parquet").load("/mnt/dndoperational/")

dnd_freetime1_v4 = dnd_freetime1_v4.withColumn("END_EVENT", trim(col("END_EVENT"))).withColumn("FT_START_EVENT", trim(col("FT_START_EVENT")))

dnd_freetime1_v4 = dnd_freetime1_v4.filter((dnd_freetime1_v4['FreightType_Cd'] == 'DET') & (dnd_freetime1_v4['ActivityExportImport'] == 'Import') & (dnd_freetime1_v4['END_EVENT'] == 'GATEIE') & ((dnd_freetime1_v4['FT_START_EVENT'] == 'DISCHARG') | (dnd_freetime1_v4['FT_START_EVENT'] == 'GATEOUTF'))).distinct()

dnd_freetime1_v4.createOrReplaceTempView("dnd_freetime1_v4")

In [ ]:
# add operational with same filters
freetime = spark.sql(""" select distinct SHIPMENT_NO, Equipment_No, FreightType_Dsc, FreightType_Cd, DischargeDate, CommoditySubType_Dsc, FreeTimeInStandardTariff_Days, FreeTimeGranted_Days, ActualTurnTime_Days from dnd_freetime1_v4 where FreightType_Dsc = 'Detention Fee - Import' and FreeTimeGranted_Days > 0 and ActualTurnTime_Days >= 0 """)
freetime.createOrReplaceTempView("freetime")


ship_free = ship_equip.join(freetime, (ship_equip.SHIPMENT_NO == freetime.SHIPMENT_NO) & (ship_equip.CONTAINER_NO == freetime.Equipment_No), 'inner').drop(freetime.SHIPMENT_NO)
ship_free.createOrReplaceTempView("ship_free")

In [ ]:
ship_free1 = spark.sql(""" select distinct *, (DischargeDate + ActualTurnTime_Days) as GateIN,  ActualTurnTime_Days as CDET_Days from ship_free where FreightType_Cd = 'DET' """)

ship_free2 = ship_free1.join(df_combination_equipment, (ship_free1.SHIPMENT_NO == df_combination_equipment.SHIPMENT_NO) & (ship_free1.CONTAINER_NO == df_combination_equipment.Equipment_No) & (ship_free1.Spot_YN == df_combination_equipment.spot_YN) ,"left").drop(df_combination_equipment.SHIPMENT_NO).drop(df_combination_equipment.Equipment_No).drop(df_combination_equipment.OPERATOR_DESC)

ship_free2.createOrReplaceTempView("ship_free2")

In [ ]:
# %sql
# select * from ship_free2 where PRICE_CALC_DT>='2023-06-01'

In [ ]:
ship_free2_df = ship_free2.toPandas()
ship_free2_df.head()

/databricks/spark/python/pyspark/sql/pandas/utils.py:105: UserWarning: The conversion of DecimalType columns is inefficient and may take a long time. Column names: [BOOKED_FFE] If those columns are not necessary, you may consider dropping them or converting to primitive types before the conversion.
  warnings.warn(


OPERATOR_DESC                  BOOKED_TS  ... spot_YN FK_AFLS_CHARGE_TYPES
0        Maersk 2021-07-05 07:29:00.959441  ...       Y                  F06
1        Maersk 2021-09-05 12:42:53.280761  ...       Y                  F13
2        Maersk 2021-09-26 02:46:17.007826  ...       Y                  F03
3        Maersk 2021-11-03 14:20:11.995676  ...       Y                  F09
4        Maersk 2021-11-12 15:13:31.853745  ...       Y                  F14

[5 rows x 27 columns]

In [ ]:
ship_free3_df = ship_free2_df.copy()

ship_free3_df['FK_AFLS_CHARGE_TYPES'] = ship_free3_df['FK_AFLS_CHARGE_TYPES'].astype(str).fillna('00')
ship_free3_df['FK_AFLS_CHARGE_TYPES'] = ship_free3_df['FK_AFLS_CHARGE_TYPES'].apply(lambda x:x[1:])

ship_free3_df.loc[ship_free3_df['FK_AFLS_CHARGE_TYPES'] == 'one', 'FK_AFLS_CHARGE_TYPES'] = '0'

ship_free3_df[['FreeTimeGranted_Days','ActualTurnTime_Days','FK_AFLS_CHARGE_TYPES']] = ship_free3_df[['FreeTimeGranted_Days', 'ActualTurnTime_Days','FK_AFLS_CHARGE_TYPES']].astype(int)

ship_free3_df['Std_FreeTimeGranted'] = ship_free3_df['FreeTimeGranted_Days'] - ship_free3_df['FK_AFLS_CHARGE_TYPES']

ship_free3_df = ship_free3_df.rename(columns={'FreeTimeGranted_Days':'Total_FreeTimeGranted_Days', 'FK_AFLS_CHARGE_TYPES':'FTEx_Taken'}).drop(['BOOKED_TS', 'BOOKED_BY_CUSTOMER_CD', 'CONTAINER_CNT', 'CONTAINER_NO', 'FreightType_Dsc'], axis=1)

ship_free3_df['Delay'] = ship_free3_df['ActualTurnTime_Days'] - ship_free3_df['Total_FreeTimeGranted_Days']

ship_free3_df.loc[ship_free3_df['Delay']<0,  'Delay'] = 0
ship_free3_df.head()

ship_free3_df = ship_free3_df[['OPERATOR_DESC','PRICE_CALC_DT','LOPFI_CITY_CD','DIPLA_CITY_CD','Import_Country','Spot_YN','CONSIGNEE_CUSTOMER_CD','SHIPMENT_NO','Equipment_No','CONTAINER_TYPE_CD', 'CONTAINER_SIZE_CD','FreightType_Cd','Std_FreeTimeGranted','Total_FreeTimeGranted_Days','FTEx_Taken','DischargeDate','GateIN','ActualTurnTime_Days','CDET_Days','Delay','CommoditySubType_Dsc','BOOKED_FFE']]

ship_free3_df = ship_free3_df.dropna()
ship_free3_df = ship_free3_df[(ship_free3_df['CDET_Days'] >= 0) & (ship_free3_df['Std_FreeTimeGranted'] > 0)]

ship_free3_df = ship_free3_df[ship_free3_df['PRICE_CALC_DT'] <= pd.to_datetime(date.today())]

ship_free3_df.head()

OPERATOR_DESC PRICE_CALC_DT  ... CommoditySubType_Dsc BOOKED_FFE
0        Maersk    2021-07-05  ...            Chemicals        0.5
1        Maersk    2021-09-05  ...                Metal        0.5
2        Maersk    2021-09-26  ...                Metal        1.0
3        Maersk    2021-11-03  ...              Tobacco        1.0
4        Maersk    2021-10-29  ...                Metal        1.0

[5 rows x 22 columns]

In [ ]:
%sql
select count(*) from dnd.cftex_v2

count(1) 20657491

In [ ]:
%sql
select count(*) from dnd.cftex_v2

count(1) 21435054

In [ ]:
ship_free3_sdf = spark.createDataFrame(ship_free3_df)
ship_free3_sdf.createOrReplaceTempView("ship_free3_sdf")
ship_free3_sdf.write.mode("overwrite").saveAsTable("dnd.cftex_v2")

/databricks/spark/python/pyspark/sql/pandas/utils.py:105: UserWarning: The conversion of DecimalType columns is inefficient and may take a long time. Column names: [BOOKED_FFE] If those columns are not necessary, you may consider dropping them or converting to primitive types before the conversion.
  warnings.warn(


In [ ]:
%sql
select * from dnd.cftex_v2

OPERATOR_DESC PRICE_CALC_DT LOPFI_CITY_CD DIPLA_CITY_CD Import_Country Spot_YN CONSIGNEE_CUSTOMER_CD SHIPMENT_NO Equipment_No CONTAINER_TYPE_CD CONTAINER_SIZE_CD FreightType_Cd Std_FreeTimeGranted Total_FreeTimeGranted_Days FTEx_Taken DischargeDate GateIN ActualTurnTime_Days CDET_Days Delay CommoditySubType_Dsc BOOKED_FFE Maersk 2022-01-05T00:00:00Z CNHSK FRLEH FR Y 111008923 1KT375315 TCKU2693040 DRY 20 DET 87 99 12 2022-04-07 2022-04-08 1 1 0 Appliances and kitchenware 0.5 Maersk 2022-02-16T00:00:00Z VEPBL CNNAN CN Y 40650190713 1KT419034 MSKU1617440 DRY 40 DET 7 14 7 2022-06-15 2022-06-23 8 8 0 Wood 1.0 Maersk 2021-10-13T00:00:00Z RULED CNSGH CN Y 40601597910 213982759 MSKU8035360 DRY 40 DET 7 14 7 2021-12-07 2021-12-13 6 6 0 Wood 1.0 Maersk 2021-10-17T00:00:00Z BRSSZ INENN IN Y 41000889742 214065868 MSKU4491485 DRY 20 DET 6 12 6 2021-12-28 2022-01-07 10 10 0 Metal 0.5 Maersk 2021-11-18T00:00:00Z INPPV SADAM SA Y 431302367 214766349 SUDU6837117 DRY 40 DET 7 10 3 2021-12-16 2021-12-26 10 10 0 Paper 1.0 Maersk 2021-11-22T00:00:00Z TRISK AEJAL AE Y 43600957338 214835393 UETU2062913 DRY 20 DET 5 10 5 2022-01-09 2022-01-19 10 10 0 Salt, sulphur, earths and stone, plastering materials, lime and cement 0.5 Maersk 2022-01-11T00:00:00Z INVTZ CNHUP CN Y 40604702351 215832553 SUDU7354983 DRY 20 DET 7 14 7 2022-02-26 2022-03-12 14 14 0 Seeds, beans, cereals and flour 0.5 Maersk 2022-02-04T00:00:00Z CIABJ INMLR IN Y 41001172062 216345945 MRKU2092252 DRY 40 DET 6 14 8 2022-04-13 2022-04-24 11 11 0 Fruit and nuts 1.0 Maersk 2022-02-05T00:00:00Z RULED SADAM SA Y 43100014086 216353244 MRKU4869608 DRY 40 DET 7 14 7 2022-05-12 2022-05-20 8 8 0 Wood 1.0 Maersk 2022-03-15T00:00:00Z INCOK QADOH QA Y 43000131656 217186580 MRKU7937619 DRY 20 DET 3 14 11 2022-04-21 2022-04-29 8 8 0 Foodstuff 0.5 Maersk 2022-03-23T00:00:00Z CNNPO CLSAI CL Y 307S1001032 217347859 MSKU4224128 DRY 20 DET 5 15 10 2022-05-16 2022-05-20 4 4 0 Plastic and rubber 0.5 Maersk 2022-03-30T00:00:00Z JPHKT NGVU2 NG Y 23300902396 217485885 PONU7999443 DRY 40 DET 14 21 7 2022-06-09 2022-06-17 8 8 0 Vehicles 1.0 Maersk 2022-04-04T00:00:00Z TZDAR CNTSK CN Y 40604693004 217599559 MSKU4185438 DRY 20 DET 7 21 14 2022-07-06 2022-07-24 18 18 0 Ores, slag and ash 0.5 Maersk 2022-05-18T00:00:00Z CNTST COBUN CO Y 30800087936 218574867 TEMU6666200 DRY 40 DET 10 14 4 2022-06-29 2022-07-15 16 16 2 Tile, stone and glass 1.0 Maersk 2022-05-24T00:00:00Z INLT4 SADAM SA Y 431302367 218732773 MRSU5239041 DRY 40 DET 7 10 3 2022-06-17 2022-06-24 7 7 0 Paper 1.0 Maersk 2022-05-25T00:00:00Z CNJJG CLSAI CL Y 30700056843 218744094 SUDU1817864 DRY 20 DET 5 14 9 2022-08-09 2022-08-17 8 8 0 Chemicals 0.5 Maersk 2022-06-09T00:00:00Z CNNPO BRIOA BR Y 30500297095 219094350 MSKU9297981 DRY 40 DET 5 19 14 2022-09-01 2022-09-09 8 8 0 Textiles and apparel 1.0 Maersk 2022-06-14T00:00:00Z CNDAI DEHAM DE Y 11300768102 219201299 MRKU7800190 DRY 20 DET 3 8 5 2022-08-31 2022-09-01 1 1 0 Tile, stone and glass 0.5 Maersk 2022-07-01T00:00:00Z TRIZM CNHSK CN Y 40601248433 219625900 MRKU7677445 DRY 20 DET 7 10 3 2022-09-01 2022-09-08 7 7 0 Ores, slag and ash 0.5 Maersk 2022-07-12T00:00:00Z INTUT LKCMB LK Y 40500020680 219825247 TCLU2393501 DRY 20 DET 10 14 4 2022-07-17 2022-08-05 19 19 5 Seeds, beans, cereals and flour 0.5 Maersk 2022-07-15T00:00:00Z CNCNQ DOZA6 DO Y 31100026302 219916244 SUDU8897795 DRY 40 DET 8 10 2 2022-10-17 2022-10-30 13 13 3 Vehicles 1.0 Maersk 2022-08-17T00:00:00Z CNSGH PABLB PA Y 325C1000277 220922060 MSKU8334057 DRY 40 DET 7 15 8 2022-10-03 2022-10-08 5 5 0 Appliances and kitchenware 1.0 Maersk 2022-09-13T00:00:00Z TZDAR ITVCE IT Y 118336394 221575780 MSKU3247978 DRY 20 DET 7 15 8 2022-11-29 2022-12-30 31 31 16 Ores, slag and ash 0.5 Maersk 2022-09-15T00:00:00Z ESBCN PYRJ6 PY Y 32600001203 221637044 HASU1110652 DRY 20 DET 8 12 4 2022-12-02 2022-12-14 12 12 0 Beverages 0.5 Maersk 2022-09-19T00:00:00Z TRIZM CNHSK CN Y 40604940224 221704146 SUDU7591645 DRY 20 DET 7 14 7 2022-12-14 2022-12-23 9 9 0 Ores, 

In [ ]:
%scala
dbutils.notebook.exit("returnValue")